In [44]:
# Model design
import agentpy as ap

# Visualization
import matplotlib.pyplot as plt
import seaborn as sns
import IPython
import pandas as pd

import random

# **Funciones auxiliares**


In [45]:
#remover tuplas vacias
def Remove(tuples):
    tuples = [t for t in tuples if t]
    return tuples

#delete tuples where first element is equal or minor to input
def deleteLeft(tuples, value):
    tuples = [t for t in tuples if t[1] >= value]
    return tuples

def deleteRight(tuples, value):
    tuples = [t for t in tuples if t[1] <= value]
    return tuples

def deleteUp(tuples, value):
    tuples = [t for t in tuples if t[0] >= value]
    return tuples

def deleteDown(tuples, value):
    tuples = [t for t in tuples if t[0] <= value]
    return tuples

In [46]:
#Donde se almacenan los datos de posicion de cada agente
results = []

# **Funcion para generar los caminos**

In [47]:
roads = []

rangos = [(0,32),(35,67),(70,102),(105,137),(140,172)] #rangos de posiciones de las calles

roads = []
rows = 173 #se le aumenta uno para evitar out of range
cols = 173
for r in range(0, rows):
  roads.append([False for c in range(0, cols)])



lista = [33,34,68,69,103,104,138,139]
for y in lista:
  for x in range(173):
    roads[y][x] = True

for y in range(173):
  for x in lista:
    roads[y][x] = True

In [ ]:
#print('\n'.join(['\t'.join([str(cell) for cell in row]) for row in roads]))

In [49]:
coordenadas_validas = []

for i in range(0, rows):
  for j in range(0, cols):
    if roads[i][j] == True:
      coordenadas_validas.append((i,j))

# **Definicion de modelos de agentes**

In [96]:
class Car(ap.Agent):
    
    def setup(self):
        self.grid = self.model.grid
        self.random = self.model.random
        self.orientation = self.random.randint(0, 3) #0 = up, 1 = right, 2 = down, 3 = left
        self.speed = 0
        self.moving = 0 # 0: none, 1: moving, 2: stopped
        self.currentPosition = ()


    def nearbyCars(self):
        neighbours = self.grid.neighbors(self, distance=6)
        neighbours = neighbours.to_list()
        
        neighbours = Remove(neighbours.currentPosition) #regresa los vecinos de la posicion actual con distancia de 6

        neighbours = sorted(neighbours, key=lambda tup: tup[0])

        return neighbours
    
    def possibleRight(self):
        #check if neighbor is not at the right of the car
        traffic = self.nearbyCars()

        traffic = deleteLeft(traffic, self.currentPosition[1]) #regresa los vecinos unicamente de la derecha

        traffic = deleteDown(traffic, self.currentPosition[0]) #regresa los vecinos unicamente de abajo
        
        traffic = deleteUp(traffic, self.currentPosition[0]) #regresa los vecinos unicamente de arriba

        #print(self.currentPosition,end = ' ') 
        #print(traffic)

        if self.currentPosition[1]+1 > 172:
            return False

        if roads[self.currentPosition[0]][self.currentPosition[1]+1]:
            if traffic:
                for car in traffic:
                    #check if the nearest car to the right is 4 spaces away
                    if car[1] > self.currentPosition[1] + 4:
                    #if car[1] > self.currentPosition[1] + 4 :
                        return True
                    else:
                        return False
            else:
                return True
        else:
            return False
    
    def possibleLeft(self):
        #check if neighbor is not at the left of the car
        traffic = self.nearbyCars()

        traffic = deleteRight(traffic, self.currentPosition[1])

        traffic = deleteDown(traffic, self.currentPosition[0]) #regresa los vecinos unicamente de abajo
        
        traffic = deleteUp(traffic, self.currentPosition[0]) #regresa los vecinos unicamente de arriba

        #print(self.currentPosition,end = ' ') 
        #print(traffic)

        if self.currentPosition[1]-1 < 0:
            return False

        if roads[self.currentPosition[0]][self.currentPosition[1]-1]:
            if traffic:
                for car in traffic:
                    #check if the nearest car to the right is 4 spaces away
                    if car[1] < self.currentPosition[1] - 4:
                        return True
                    else:
                        return False
            else:
                return True
        else:
            return False

    def possibleUp(self):
        #check if neighbor is not at the right of the car
        traffic = self.nearbyCars()

        traffic = deleteLeft(traffic, self.currentPosition[1]) #regresa los vecinos unicamente de la derecha
        traffic = deleteRight(traffic, self.currentPosition[1])
        traffic = deleteDown(traffic, self.currentPosition[0]) #regresa los vecinos unicamente de abajo

        if self.currentPosition[0]-1 < 0:
            return False

        if roads[self.currentPosition[0]-1][self.currentPosition[1]]:
            if traffic:
                for car in traffic:
                    #check if the nearest car to the right is 4 spaces away
                    if car[0] < self.currentPosition[0] - 4:
                        return True
                    else:
                        return False
            else:
                return True
        else:
            return False

    def possibleDown(self):
        #check if neighbor is not at the right of the car
        traffic = self.nearbyCars()

        traffic = deleteLeft(traffic, self.currentPosition[1]) #regresa los vecinos unicamente de la derecha
        traffic = deleteRight(traffic, self.currentPosition[1])
        traffic = deleteUp(traffic, self.currentPosition[0]) #regresa los vecinos unicamente de abajo

        if self.currentPosition[0]-1 < 0:
            return False

        if roads[self.currentPosition[0]-1][self.currentPosition[1]]:
            if traffic:
                for car in traffic:
                    #check if the nearest car to the right is 4 spaces away
                    if car[0] > self.currentPosition[0] - 4:
                        return True
                    else:
                        return False
            else:
                return True
        else:
            return False

    #Identifica si se encuentra en una calle exterior o no
    def outterStr(self):
        if(self.currentPosition[0] > 34 and self.currentPosition[0] < 138):
            if(self.currentPosition[1] > 34 and self.currentPosition[1] < 138):
                return False
        
        return True
    
    #Revisa que no quiera entrar a una calle interior incorrecta desde una calle exterior
    def outerEntry(self):
        if(self.currentPosition[1] in [103, 104] and self.currentPosition[0] == 69):
            return False
        elif(self.currentPosition[0] in [103, 104] and self.currentPosition[1] == 103):
            return False
        elif(self.currentPosition[1] in [68, 69] and self.currentPosition[0] == 103):
            return False
        elif(self.currentPosition[0] in [68, 69] and self.currentPosition[1] == 69):
            return False
        return True
        
    def moveRight(self):
        #FALTA check if there is a neighbor to the right
        self.orientation = 1

        if(self.possibleRight()):
            self.angle = 0
            self.grid.move_to(self,(self.currentPosition[0],self.currentPosition[1]+1))
            self.currentPosition = self.grid.positions[self]

    def moveLeft(self):
        #FALTA check if there is a neighbor to the left
        self.orientation = 3
        if(self.possibleLeft()):
            self.angle = 2
            self.grid.move_to(self,(self.currentPosition[0],self.currentPosition[1]-1))
            self.currentPosition = self.grid.positions[self]

    def moveUp(self):
        #FALTA check if there is a neighbor to the left
        self.orientation = 0
        if(self.possibleUp()):
            self.angle = 1
            self.grid.move_to(self,(self.currentPosition[0]-1,self.currentPosition[1]))
            self.currentPosition = self.grid.positions[self]

    def moveDown(self):
        self.orientation = 2
        #FALTA check if there is a neighbor to the left
        if(self.possibleDown()):
            self.angle = 3
            self.grid.move_to(self,(self.currentPosition[0]+1,self.currentPosition[1]))
            self.currentPosition = self.grid.positions[self]

    def move(self):
        #checa si no esta definida la tupla de posicion
        if not self.currentPosition:
            self.currentPosition = self.grid.positions[self]

        #cambia estado a en movimiento
        self.moving = 1

        agentYDirection = self.currentPosition[0]
        agentXDirection = self.currentPosition[1]

        movement = self.random.randint(0, 1)

        #Movement: 0 ==> Movimiento vertical    |     1 ===> Movimiento horizontal
        
        if(self.outterStr()): #Movimiento en calles exteriores
            if movement == 0:
                    if(agentXDirection in [33,34, 68,69]):
                        if(self.outerEntry()):
                            self.moveDown()
                    else:
                        if(self.outerEntry()):
                            self.moveUp()
            elif movement == 1:
                    if(agentYDirection in [33, 34, 68, 69]):
                        if(self.outerEntry()):
                            self.moveLeft()
                    else:
                        if(self.outerEntry()):
                            self.moveRight()

        else: #Movimiento en calles interiores arreglar
            if movement == 1:
                if(agentYDirection in [103, 68, 69] and agentYDirection in [70,105]):
                    self.moveLeft()
                    self.moveDown()
                if(agentYDirection in [104, 68, 69] and agentXDirection in [67,102]):
                    self.moveRight()
                    self.moveUp()
            else:
                if(agentXDirection in [103,104,68,69] and agentYDirection in [105,70]):
                    self.moveUp()
                    self.moveLeft()   
                if(agentXDirection in [68,69,103,104] and agentYDirection in [67,102]):
                    #self.moveDown()
                    self.moveRight()

        '''
        #comportamiento de las bicicletas
        else:   #Movimiento en calles interiores
            if movement == 0: 
                if(agentXDirection in [68, 69]):
                    if(agentYDirection > 69 and agentYDirection < 105 and agentXDirection == 68):
                        self.moveUp()
                    elif(agentYDirection > 69 and agentYDirection < 103):
                        self.moveUp()
                    else:
                        self.moveDown()
                else:
                    if(agentYDirection > 67 and agentYDirection < 103 and agentXDirection == 104):
                        self.moveDown()
                    elif(agentYDirection > 69 and agentYDirection < 103):
                        self.moveDown()
                    else:
                        self.moveUp()
            if movement == 1:
                if(agentYDirection in [68, 69]):
                    if(agentXDirection > 69 and agentYDirection < 105 and agentYDirection == 68):
                        self.moveRight()
                    elif(agentXDirection > 69 and agentXDirection < 103):
                        self.moveRight()
                    else:
                        self.moveLeft()
                else:
                    if(agentXDirection > 67 and agentYDirection < 103 and agentYDirection == 104):
                        self.moveLeft()
                    elif(agentXDirection > 69 and agentXDirection < 103):
                        self.moveLeft()
                    else:
                        self.moveRight()
        '''
        
        self.currentPosition = self.grid.positions[self]

        

In [84]:
nCars = 50
amountOfPoints = len(coordenadas_validas)

#generate list of size nCars with random unique valid positions
carPositions = []
for i in range(nCars):
    position = coordenadas_validas[random.randint(0, amountOfPoints-1)]
    carPositions.append(position)

#print(carPositions)

class SuperBlockModel(ap.Model):
    def setup(self):
        s = self.p.size
        n = self.p.cars

        #Create grid and agents
        self.grid = ap.Grid(self, (s, s), track_empty=True)
        self.agents = ap.AgentList(self, n, Car)
        self.grid.add_agents(self.agents, positions = carPositions, random=True, empty=True)

    def update(self):
        self.agents.move()    
    
    def step(self):
        # Move agents
        self.agents.move()   
         

        # Update grid
        #comentar esto durante el desarrollo

        result = []
        
        for agent in self.agents:
            result.append(agent.currentPosition)

        results.append(result)


In [76]:
parameters = {
    'cars': nCars,
    'size': 173, # Size of the grid
    'steps': 150  # Maximum number of steps
}

In [97]:
# Create single-run animation with custom colors

def animation_plot(model, ax):
    group_grid = model.grid.attr_grid('moving')
    color_dict = {0:'#7FC97F' ,1:'#ffff', 2:"#fe4450", None:'#343131'}
    ap.gridplot(group_grid, ax=ax, color_dict=color_dict, convert=True)
    ax.set_title("Modelo SuperManzanas")

fig, ax = plt.subplots()
model = SuperBlockModel(parameters)
animation = ap.animate(model, fig, ax, animation_plot)
IPython.display.HTML(animation.to_jshtml(fps=60))

# **Exportar resultados**

Esta opcion no es recomendable usarla durante el desarrollo ya que tiene que guardar 173**2 por el numero de steps

In [86]:
resultados = pd.DataFrame(results)

#export to csv
resultados.to_csv('resultados.csv')

In [91]:
jsonFinal = resultados.to_json('temp.json', orient='records', lines=True)